In [1]:
%run ../ipynb_util_tars.py

In [2]:
%run ../ipynb_load_data_natural.py

{'SDG': Value(dtype='int64', id=None), 'ABSTRACT': Value(dtype='string', id=None), 'id': Value(dtype='string', id=None), 'sdg_desc_short': Value(dtype='string', id=None), 'sdg_desc_long': Value(dtype='string', id=None), '__index_level_0__': Value(dtype='int64', id=None)}
Example instance:	 {'SDG': 8, 'ABSTRACT': 'The scheme gives enterprises with business activity in Norway a tax credit on their R&D projects. The R&D content must be approved by the Research Council of Norway ex ante. In 2009, the cap on expenses per enterprise for intramural R&D projects increased to NOK 5.5 million (previously it was N0K 4 million), and NOK11 million (previously it was NOK 8 million) for projects conducted at an R&D institution.', 'id': None, 'sdg_desc_short': None, 'sdg_desc_long': None, '__index_level_0__': 492}
id2label: {0: '1', 1: '2', 2: '3', 3: '4', 4: '5', 5: '6', 6: '7', 7: '8', 8: '9', 9: '10', 10: '11', 11: '12', 12: '13', 13: '14', 14: '15', 15: '16', 16: '17'}
label2id: {'1': 0, '2': 1, '

## Load SciBERT

In [3]:
import transformers
from transformers import AutoTokenizer, AutoModelForSequenceClassification

# load the best model
MODEL_PATH = CHECKPOINT_PATH + "/final/allenai/scibert_scivocab_uncased-zo_up/checkpoint-316"
model = AutoModelForSequenceClassification.from_pretrained(
    MODEL_PATH,
    id2label=id2label,
    label2id=label2id
)
tokenizer = AutoTokenizer.from_pretrained(MODEL_PATH)
model.eval()

pred = transformers.pipeline(
    "text-classification",
    model=model,
    batch_size=8,
    tokenizer=tokenizer,
    truncation=True,
    padding=True,
    max_length=512,
    device=0,
    top_k=None,     # equal to return_all_scores=True
)

# PartitionShap

In [4]:
sample_sentence = """These processes are essential to the functioning of the natural environment and as a result, water stress can arise when the amount of water in the environment is insufficient for natural environmental processes to function and deliver the services on which people, flora and fauna depend. Typically, “environmental water requirements” are treated as a residual (King and Brown 2011), and as a result, the lack of water available for environmental needs is creating serious environmental problems. For instance, due to extensive water extractions, some large rivers in semi-arid locations, such as the Colorado and the Murray, only intermittently reach the sea (King and Brown, 2011), and the reduced flows in rivers and water volumes in lakes and wetlands has had a major negative impact on ecosystems. This transformation has also greatly reduced the water quality of the remaining water making it much more saline."""

In [5]:
pred([sample_sentence])

[[{'label': '6', 'score': 0.4347546696662903},
  {'label': '14', 'score': 0.1369265466928482},
  {'label': '13', 'score': 0.06695637851953506},
  {'label': '11', 'score': 0.04988940432667732},
  {'label': '7', 'score': 0.0428665466606617},
  {'label': '12', 'score': 0.03380381315946579},
  {'label': '15', 'score': 0.03314424306154251},
  {'label': '2', 'score': 0.02874414250254631},
  {'label': '1', 'score': 0.027402125298976898},
  {'label': '4', 'score': 0.025833608582615852},
  {'label': '9', 'score': 0.02543775737285614},
  {'label': '17', 'score': 0.02458510547876358},
  {'label': '10', 'score': 0.017064973711967468},
  {'label': '3', 'score': 0.01563967764377594},
  {'label': '16', 'score': 0.015530998818576336},
  {'label': '8', 'score': 0.011303692124783993},
  {'label': '5', 'score': 0.0101163936778903}]]

In [6]:
import shap

explainer = shap.Explainer(pred, output_names=[f"SDG {i+1}" for i in range(17)])
shap_values = explainer([sample_sentence])

You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


In [7]:
shap.plots.text(shap_values[0, :, :], xmin=-1, xmax=1)